In [1]:
import pandas as pd
import stanza
import numpy as np
from stanza.models.common.doc import Word

In [2]:
nlp=stanza.Pipeline("hu",processors='tokenize,pos,lemma,depparse')

2022-05-27 22:12:51 INFO: Loading these models for language: hu (Hungarian):
| Processor | Package |
-----------------------
| tokenize  | szeged  |
| pos       | szeged  |
| lemma     | szeged  |
| depparse  | szeged  |

2022-05-27 22:12:51 INFO: Use device: cpu
2022-05-27 22:12:51 INFO: Loading: tokenize
2022-05-27 22:12:52 INFO: Loading: pos
2022-05-27 22:12:52 INFO: Loading: lemma
2022-05-27 22:12:52 INFO: Loading: depparse
2022-05-27 22:12:52 INFO: Done loading processors!


In [7]:
text="Mi nem vagyunk magyarok."
text="− Én sem értem, hogy miért keresek ma mindent."
text="Koridor itu beraroma kubis rebus dan karpet butut."
text="Pada mulanya, waktu Allah mulai menciptakan alam semesta"
text='dan dinamakan-Nya terang itu "Siang" dan gelap itu "Malam"'
text="Koridor itu beraroma kubisnya rebus dan karpet butut."
text="Apakah Allah benar-benar, melarang :e: terbesar terjelas kalian-nya makan buah-buahan dari segala pohon di taman ini?"
text="WAKTU itu musim semi tahun 1894. Seluruh dikenal dilakukan penduduk kota London gempar atas terbunuhnya"
text="A nagyon szép nőhöz megyem. kitörésröl kitörésekre Amerikából"
text= "Kazahsztánban a mai kazak nyelv cirill betűs írást használ."# Közeli rokonai a kirgiz, a tatár, a baskír, valamint a kihalt besenyő és kun nyelvek."

In [8]:
doc = nlp(text) 
wordlist=pd.concat([pd.Series(word.to_dict()).to_frame().T for sentence in doc.sentences for word in sentence.words])
wordlist

id           text       lemma   upos  \
0   1  Kazahsztánban  Kazahsztán  PROPN   
0   2              a           a    DET   
0   3            mai         mai    ADJ   
0   4          kazak       kazak    ADJ   
0   5          nyelv       nyelv   NOUN   
0   6         cirill      cirill    ADJ   
0   7          betűs       betűs    ADJ   
0   8          írást        írás   NOUN   
0   9        használ     használ   VERB   
0  10              .           .  PUNCT   

                                               feats head    deprel  \
0                               Case=Ine|Number=Sing    9       obl   
0                          Definite=Def|PronType=Art    5       det   
0                    Case=Nom|Degree=Pos|Number=Sing    5  amod:att   
0                    Case=Nom|Degree=Pos|Number=Sing    5  amod:att   
0                               Case=Nom|Number=Sing    9     nsubj   
0                    Case=Nom|Degree=Pos|Number=Sing    8  amod:att   
0                    Case=Nom|Degree=Pos|Number=Sing    8  amod:att   
0                               Case=Acc|Number=Sing    9       obj   
0  Definite=Ind|Mood=Ind|Number=Sing|Person=3|Ten...    0      root   
0                                                NaN    9     punct   

  start_char end_char  
0          0       13  
0         14       15  
0         16       19  
0         20       25  
0         26       31  
0         32       38  
0         39       44  
0         45       50  
0         51       58  
0         58       59

In [5]:
wordlist.iloc[4]["feats"]

'Definite=Ind|Mood=Ind|Number=Sing|Person=3|Tense=Pres|VerbForm=Fin|Voice=Act'

In [21]:
folder="~/Desktop/Regina Phalange/Conlang/"
dic=pd.read_csv(folder+"dict.csv",sep=";")
lemmadict=dict(zip(dic["lemma"],dic["translation"]))
capitalize_get = lambda x : x["text"][0].isupper()
wordlist["capitalize"] = wordlist[["text"]].apply(capitalize_get, axis=1)
capitalize_apply = lambda x,y : x[0].upper()+x[1:] if y else x
def lemmadictget (x):
    if x["upos"]!="PUNCT":
        if x["lemma"] in lemmadict.keys():
            return capitalize_apply(lemmadict[x["lemma"]], x["capitalize"])
        else:
            return "*"+capitalize_apply(x["lemma"], x["capitalize"])
    else:
        return x["text"]

wordlist["translemma"] = wordlist[["lemma","upos","text","capitalize"]].apply(lemmadictget, axis=1)


wordlist['end_char_prev'] = np.roll(wordlist['end_char'],1)
wordlist.iloc[0]['end_char_prev']=0
wordlist["separator_prev"]=wordlist[["end_char_prev","start_char"]].apply(lambda x: text[x["end_char_prev"]:x["start_char"]], axis=1)

sep_end=text[wordlist.iloc[-1]["end_char"]]
print("".join(list(wordlist["separator_prev"]+wordlist["translemma"])+[sep_end]))

/home/maxwell/.local/lib/python3.8/site-packages/pandas/core/series.py:1056: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cacher_needs_updating = self._check_is_chained_assignment_possible()


IndexError: string index out of range

In [ ]:


# depict
pd.set_option("display.max_rows", None, "display.max_columns", None)
print(wordlist)
import networkx as nx
import graphviz
w = graphviz.Digraph()
for i,row in wordlist.iterrows(): w.node(str(row["id"]), "\n".join(row[:-2].apply(str)))

for i,row in wordlist.iterrows(): w.edge(str(row["id"]), str(row["head"]))

w.render('test-output/round-table.gv', view=True)

folder="~/Desktop/Regina Phalange/Conlang/"
dic=pd.read_csv(folder+"dict.csv",sep=";")
lemmadict=dict(zip(dic["lemma"],dic["translation"]))
capitalize_get = lambda x : x["text"][0].isupper()
wordlist["capitalize"] = wordlist[["text"]].apply(capitalize_get, axis=1)
capitalize_apply = lambda x,y : x[0].upper()+x[1:] if y else x
def lemmadictget (x):
    if x["upos"]!="PUNCT":
        if x["lemma"] in lemmadict.keys():
            return capitalize_apply(lemmadict[x["lemma"]], x["capitalize"])
        else:
            return "*"+capitalize_apply(x["lemma"], x["capitalize"])
    else:
        return x["text"]

wordlist["translemma"] = wordlist[["lemma","upos","text","capitalize"]].apply(lemmadictget, axis=1)


wordlist['end_char_prev'] = np.roll(wordlist['end_char'],1)
wordlist.iloc[0]['end_char_prev']=0
wordlist["separator_prev"]=wordlist[["end_char_prev","start_char"]].apply(lambda x: text[x["end_char_prev"]:x["start_char"]], axis=1)

sep_end=text[wordlist.iloc[-1]["end_char"]]
print("".join(list(wordlist["separator_prev"]+wordlist["translemma"])+[sep_end]))

In [43]:
import unimorph as um

In [46]:
um.download_unimorph(lang="ru")

Cloning into 'ru'...
fatal: could not read Username for 'https://github.com': No such device or address


CalledProcessError: Command '['git', 'clone', 'https://github.com/unimorph/ru.git']' returned non-zero exit status 128.

In [45]:
um.analyze_word("свистишь", lang="ru")

Cloning into 'ru'...
fatal: could not read Username for 'https://github.com': No such device or address


CalledProcessError: Command '['git', 'clone', 'https://github.com/unimorph/ru.git']' returned non-zero exit status 128.